# Imports

In [1]:
import os
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
import xgboost as xgb
import lightgbm as lgb
import catboost as cb
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import accuracy_score, roc_auc_score, confusion_matrix, classification_report, roc_curve, auc
import joblib
import optuna
import mlflow
import matplotlib.pyplot as plt
import seaborn as sns
import shap
from tqdm import tqdm

/usr/local/lib/python3.8/dist-packages/xgboost/core.py:265: FutureWarning: Your system has an old version of glibc (< 2.28). We will stop supporting Linux distros with glibc older than 2.28 after **May 31, 2025**. Please upgrade to a recent Linux distro (with glibc 2.28+) to use future versions of XGBoost.
Note: You have installed the 'manylinux2014' variant of XGBoost. Certain features such as GPU algorithms or federated learning are not available. To use these features, please upgrade to a recent Linux distro with glibc 2.28+, and install the 'manylinux_2_28' variant.
  warnings.warn(


# Settings

In [24]:
# Exports
LOCAL_EXPORT_FOLDER_PATH='/content/exports'
# Exports > Manual check path 
LOCAL_EXPORT_MANUAL_CHECK_PATCH_FOLDER_PATH=LOCAL_EXPORT_FOLDER_PATH+'/manual_check_patch'
TARGET_COLUMNS=['TARGET',]
LOCAL_EXPORT_MODELIZATION_FOLDER_PATH=LOCAL_EXPORT_FOLDER_PATH+'/modelization'
MLFLOW_EXPERIMENT_NAME = 'generic_model_experiment'
LOCAL_EXPORT_MODELIZATION_EVALUATION_RESULT_FOLDER_PATH=LOCAL_EXPORT_FOLDER_PATH+'/modelization_evaluation'

# Export > General Settings
TESTING_MODE=True
TESTING_MODE_MAX_LINES=1000
TESTING_MODE_SUB_FOLDER_NAME='testing_data'
GENERAL_CHUNK_SIZE=100000


In [3]:
def display_head_of_files(base_path, file_extension='csv', chunk_size=1000):
    """
    Parcours tous les fichiers dans le répertoire donné et affiche les premières lignes de chaque fichier CSV.

    Args:
        base_path (str): Le chemin du répertoire de base où se trouvent les fichiers.
        file_extension (str): L'extension des fichiers à traiter (par défaut 'csv').
        chunk_size (int): Taille des chunks pour lire les fichiers partiellement.

    Returns:
        None
    """
    for root, dirs, files in os.walk(base_path):
        for file in files:
            if file.endswith(file_extension):
                file_path = os.path.join(root, file)
                print(f"Processing file: {file_path}")
                
                # Lire les premières lignes du fichier CSV
                for chunk in pd.read_csv(file_path, chunksize=chunk_size):
                    print(chunk.head())
                    break  # On ne lit qu'un seul chunk pour obtenir le head
                print("\n" + "="*80 + "\n")

# Exemple d'utilisation

In [ ]:
display_head_of_files(base_path=LOCAL_EXPORT_MANUAL_CHECK_PATCH_FOLDER_PATH)

# Models

In [50]:
# Liste des modèles et leurs hyperparamètres
models = {
    'Logistic Regression': {
        'model': LogisticRegression(),
        'params': {
            'C': np.logspace(-3, 3, 7),
            'solver': ['newton-cg', 'lbfgs', 'liblinear']
        }
    },
    'Random Forest': {
        'model': RandomForestClassifier(),
        'params': {
            'n_estimators': [100, 200, 300],
            'max_depth': [10, 20, 30],
            'min_samples_split': [2, 5, 10],
            'min_samples_leaf': [1, 2, 4]
        }
    },
    'Gradient Boosting': {
        'model': GradientBoostingClassifier(),
        'params': {
            'n_estimators': [100, 200, 300],
            'learning_rate': [0.01, 0.05, 0.1],
            'max_depth': [3, 4, 5],
            'subsample': [0.8, 0.9, 1.0]
        }
    },
    'XGBoost': {
        'model': xgb.XGBClassifier(use_label_encoder=False, eval_metric='logloss'),
        'params': {
            'n_estimators': [100, 200, 300],
            'learning_rate': [0.01, 0.05, 0.1],
            'max_depth': [3, 4, 5],
            'colsample_bytree': [0.3, 0.7]
        }
    },
    # 'LightGBM': {
    #     'model': lgb.LGBMClassifier(),
    #     'params': {
    #         'n_estimators': [100, 200, 300],
    #         'learning_rate': [0.01, 0.05, 0.1],
    #         'num_leaves': [31, 62, 127],
    #         'boosting_type': ['gbdt', 'dart']
    #     }
    # },
    # 'CatBoost': {
    #     'model': cb.CatBoostClassifier(verbose=0),
    #     'params': {
    #         'iterations': [100, 200, 300],
    #         'learning_rate': [0.01, 0.05, 0.1],
    #         'depth': [3, 4, 5],
    #         'l2_leaf_reg': [3, 5, 7]
    #     }
    # },
    # 'SVM': {
    #     'model': SVC(probability=True),
    #     'params': {
    #         'C': np.logspace(-3, 3, 7),
    #         'kernel': ['linear', 'rbf', 'poly'],
    #         'degree': [3, 4, 5]
    #     }
    # },
    # 'KNN': {
    #     'model': KNeighborsClassifier(),
    #     'params': {
    #         'n_neighbors': [5, 10, 20],
    #         'weights': ['uniform', 'distance'],
    #         'metric': ['euclidean', 'manhattan']
    #     }
    # },
    # 'Neural Network': {
    #     'model': MLPClassifier(max_iter=500),
    #     'params': {
    #         'hidden_layer_sizes': ['50,50', '100', '100,50'],
    #         'activation': ['tanh', 'relu'],
    #         'alpha': [0.0001, 0.001, 0.01]
    #     }
    # }
}

# Entrainment

## Hyperparameter optimization method

In [6]:
# Fonction d'optimisation des hyperparamètres avec Optuna
def objective(trial, X_train, y_train):
    classifier_name = trial.suggest_categorical('classifier', list(models.keys()))
    classifier_info = models[classifier_name]
    classifier = classifier_info['model']
    params = classifier_info['params']

    trial_params = {}
    for param, values in params.items():
        if param == 'hidden_layer_sizes':
            hidden_layer_size_str = trial.suggest_categorical(param, values)
            trial_params[param] = tuple(map(int, hidden_layer_size_str.split(',')))
        elif isinstance(values[0], int):
            trial_params[param] = trial.suggest_int(param, min(values), max(values))
        elif isinstance(values[0], float):
            trial_params[param] = trial.suggest_float(param, min(values), max(values))
        else:
            trial_params[param] = trial.suggest_categorical(param, values)
    
    classifier.set_params(**trial_params)
    
    pipeline = Pipeline(steps=[
        ('classifier', classifier)
    ])
    
    score = cross_val_score(pipeline, X_train, y_train, n_jobs=-1, cv=5, scoring='accuracy', error_score='raise')
    accuracy = score.mean()
    return accuracy

## Optuna optimize hyperameters

In [7]:
# Fonction d'optimisation des hyperparamètres avec Optuna
def objective(trial, X_train, y_train):
    classifier_name = trial.suggest_categorical('classifier', list(models.keys()))
    classifier_info = models[classifier_name]
    classifier = classifier_info['model']
    params = classifier_info['params']

    trial_params = {}
    for param, values in params.items():
        if param == 'hidden_layer_sizes':
            hidden_layer_size_str = trial.suggest_categorical(param, values)
            trial_params[param] = tuple(map(int, hidden_layer_size_str.split(',')))
        elif isinstance(values[0], int):
            trial_params[param] = trial.suggest_int(param, min(values), max(values))
        elif isinstance(values[0], float):
            trial_params[param] = trial.suggest_float(param, min(values), max(values))
        else:
            trial_params[param] = trial.suggest_categorical(param, values)
    
    classifier.set_params(**trial_params)
    
    pipeline = Pipeline(steps=[
        ('classifier', classifier)
    ])
    
    score = cross_val_score(pipeline, X_train, y_train, n_jobs=-1, cv=5, scoring='accuracy', error_score='raise')
    accuracy = score.mean()
    return accuracy

# Re-entrainment method for best increase

In [8]:
# Fonction pour ré-entraîner un modèle jusqu'à atteindre une amélioration significative
def retrain_model(best_pipeline, X_train, y_train, X_test, y_test, threshold=0.01, max_iter=10):
    previous_score = 0
    for iteration in range(max_iter):
        best_pipeline.fit(X_train, y_train)
        y_pred = best_pipeline.predict(X_test)
        current_score = accuracy_score(y_test, y_pred)
        improvement = current_score - previous_score
        if improvement < threshold:
            break
        previous_score = current_score
        print(f"Iteration {iteration + 1}, Accuracy: {current_score}, Improvement: {improvement}")
    return best_pipeline, current_score

## Principal to entrain model

In [57]:
# Fonction d'optimisation des hyperparamètres avec Optuna
def objective(trial, X_train, y_train):
    classifier_name = trial.suggest_categorical('classifier', list(models.keys()))
    classifier_info = models[classifier_name]
    classifier = classifier_info['model']
    params = classifier_info['params']

    trial_params = {}
    for param, values in params.items():
        if param == 'hidden_layer_sizes':
            hidden_layer_size_str = trial.suggest_categorical(param, values)
            trial_params[param] = tuple(map(int, hidden_layer_size_str.split(',')))
        elif isinstance(values[0], int):
            trial_params[param] = trial.suggest_int(param, min(values), max(values))
        elif isinstance(values[0], float):
            trial_params[param] = trial.suggest_float(param, min(values), max(values))
        else:
            trial_params[param] = trial.suggest_categorical(param, values)
    
    classifier.set_params(**trial_params)
    
    pipeline = Pipeline(steps=[
        ('classifier', classifier)
    ])
    
    score = cross_val_score(pipeline, X_train, y_train, n_jobs=-1, cv=5, scoring='accuracy', error_score='raise')
    accuracy = score.mean()
    return accuracy

# Fonction pour ré-entraîner un modèle jusqu'à atteindre une amélioration significative
def retrain_model(best_pipeline, X_train, y_train, threshold=0.01, max_iter=10):
    previous_score = 0
    for iteration in range(max_iter):
        best_pipeline.fit(X_train, y_train)
        y_pred = best_pipeline.predict(X_train)
        current_score = accuracy_score(y_train, y_pred)
        improvement = current_score - previous_score
        if improvement < threshold:
            break
        previous_score = current_score
        print(f"Iteration {iteration + 1}, Accuracy: {current_score}, Improvement: {improvement}")
    return best_pipeline, current_score

def train_and_evaluate_models(base_path, output_folder, target_columns, max_features=5, testing=False, chunk_size=1000, testing_sub_path_name='test'):
    all_scores = {}
    total_files = sum([len(files) for r, d, files in os.walk(base_path) if any(f.endswith('application_train.csv') for f in files)])
    pbar = tqdm(total=total_files, desc="Processing files")

    for root, dirs, files in os.walk(base_path):
        for file in files:
            if file.endswith('application_train.csv'):
                file_path = os.path.join(root, file)
                test_file_path = file_path.replace('application_train.csv', 'application_test.csv')

                print(f"Processing file: {file_path}")

                # Lire les fichiers CSV par chunks
                for chunk in pd.read_csv(file_path, chunksize=chunk_size):
                    test_data = pd.read_csv(test_file_path)

                    for target_column in target_columns:
                        print(f"Using target column: {target_column}")

                        # Calculer les corrélations et sélectionner les meilleures caractéristiques
                        correlations = chunk.corr()[target_column].abs().sort_values(ascending=False)
                        top_features = correlations.index[1:max_features+1].tolist()

                        # Séparation des features et de la cible
                        X_train = chunk[top_features]
                        y_train = chunk[target_column]

                        X_test = test_data[top_features]
                        y_test = test_data[target_column] if target_column in test_data.columns else None

                        # Vérifier le nombre de classes dans y_train
                        if y_train.nunique() < 2:
                            print(f"Skipping optimization for {target_column} as it contains only one class in the training data.")
                            continue

                        # Optimisation des hyperparamètres avec Optuna
                        study = optuna.create_study(direction='maximize')
                        study.optimize(lambda trial: objective(trial, X_train, y_train), n_trials=100)

                        print('Number of finished trials: ', len(study.trials))
                        print('Best trial:')
                        trial = study.best_trial

                        print('  Value: ', trial.value)
                        print('  Params: ')
                        for key, value in trial.params.items():
                            print('    {}: {}'.format(key, value))

                        # Entraîner le meilleur modèle
                        best_classifier_name = trial.params['classifier']
                        best_classifier_info = models[best_classifier_name]
                        best_classifier = best_classifier_info['model']
                        best_params = {k: v for k, v in trial.params.items() if k != 'classifier'}

                        best_classifier.set_params(**best_params)

                        # Création du pipeline avec le meilleur modèle
                        best_pipeline = Pipeline(steps=[
                            ('classifier', best_classifier)
                        ])

                        # Retrain the model with the entire training dataset
                        best_pipeline, _ = retrain_model(best_pipeline, X_train, y_train)

                        # Déterminer le chemin de sortie
                        relative_path = os.path.relpath(root, base_path)
                        
                        output_dir = os.path.join(output_folder, relative_path, target_column)

                        if not os.path.exists(output_dir):
                            os.makedirs(output_dir)

                        model_path = os.path.join(output_dir, f'best_{best_classifier_name}_model.pkl')
                        joblib.dump(best_pipeline, model_path)

                        # Enregistrer les données de test
                        test_data_path = os.path.join(output_dir, 'test_data.csv')
                        test_data[top_features].to_csv(test_data_path, index=False)

                        if y_test is not None:
                            # Évaluation du modèle
                            y_pred = best_pipeline.predict(X_test)
                            y_pred_proba = best_pipeline.predict_proba(X_test)[:, 1]  # Only use the probability for the positive class
                            accuracy = accuracy_score(y_test, y_pred)
                            roc_auc = roc_auc_score(y_test, y_pred_proba)

                            print(f"Accuracy: {accuracy}")
                            print(f"ROC AUC: {roc_auc}")
                            print(confusion_matrix(y_test, y_pred))
                            print(classification_report(y_test, y_pred))

                            # Logging avec mlflow
                            mlflow.set_experiment('credit_scoring')
                            with mlflow.start_run():
                                mlflow.log_params(trial.params)
                                mlflow.log_metric('accuracy', accuracy)
                                mlflow.log_metric('roc_auc', roc_auc)
                                mlflow.sklearn.log_model(best_pipeline, 'model')
                                mlflow.log_artifact(file_path)
                                mlflow.log_artifact(test_file_path)
                                mlflow.log_artifact(test_data_path)

                        print(f'Model saved at {model_path}')
                
                pbar.update(1)

    pbar.close()

    # Visualisation des scores de validation croisée
    model_names = list(all_scores.keys())
    model_scores = [score for scores in all_scores.values() for score in scores]
    model_names_repeated = [model for model in model_names for _ in range(len(all_scores[model]))]

    plot_cross_val_scores(model_scores, model_names_repeated, output_folder)

# Fonction de visualisation pour les scores de validation croisée
def plot_cross_val_scores(model_scores, model_names, output_dir):
    plt.figure(figsize=(12, 8))
    sns.boxplot(x=model_names, y=model_scores)
    plt.xlabel('Model')
    plt.ylabel('Cross-Validation Score')
    plt.title('Model Comparison - Cross-Validation Scores')
    plt.xticks(rotation=45)
    plt.savefig(os.path.join(output_dir, 'cross_val_scores.png'))
    plt.close()

## Calling modelization method

In [58]:
train_and_evaluate_models(
    base_path=LOCAL_EXPORT_MANUAL_CHECK_PATCH_FOLDER_PATH, 
    output_folder=LOCAL_EXPORT_MODELIZATION_FOLDER_PATH, 
    target_columns=TARGET_COLUMNS, 
    testing=TESTING_MODE, 
    chunk_size=GENERAL_CHUNK_SIZE, 
    testing_sub_path_name=TESTING_MODE_SUB_FOLDER_NAME)


Processing files:   0%|          | 0/270 [00:00<?, ?it/s][I 2024-07-08 15:30:13,393] A new study created in memory with name: no-name-a8041cc1-816c-4480-b8a2-ddcea49b3218


Processing file: /content/exports/manual_check_patch/testing_data/mean/LOF/ordinal/application_train.csv
Using target column: TARGET


[I 2024-07-08 15:30:14,673] Trial 0 finished with value: 0.9181818181818182 and parameters: {'classifier': 'Logistic Regression', 'C': 552.4138310166662, 'solver': 'liblinear'}. Best is trial 0 with value: 0.9181818181818182.
[I 2024-07-08 15:30:15,252] Trial 1 finished with value: 0.9136363636363635 and parameters: {'classifier': 'XGBoost', 'n_estimators': 147, 'learning_rate': 0.09283774331258096, 'max_depth': 4, 'colsample_bytree': 0.44408751279305125}. Best is trial 0 with value: 0.9181818181818182.
[I 2024-07-08 15:30:15,858] Trial 2 finished with value: 0.9181818181818182 and parameters: {'classifier': 'Logistic Regression', 'C': 668.7020372706857, 'solver': 'newton-cg'}. Best is trial 0 with value: 0.9181818181818182.
[I 2024-07-08 15:30:16,319] Trial 3 finished with value: 0.9181818181818182 and parameters: {'classifier': 'Logistic Regression', 'C': 162.92946738209884, 'solver': 'lbfgs'}. Best is trial 0 with value: 0.9181818181818182.
[I 2024-07-08 15:30:16,590] Trial 4 finish

Number of finished trials:  100
Best trial:
  Value:  0.9227272727272726
  Params: 
    classifier: Logistic Regression
    C: 1.0328132125486604
    solver: newton-cg
Iteration 1, Accuracy: 0.9227272727272727, Improvement: 0.9227272727272727
Model saved at /content/exports/modelization/testing_data/mean/LOF/ordinal/TARGET/best_Logistic Regression_model.pkl
Processing file: /content/exports/manual_check_patch/testing_data/mean/LOF/label/application_train.csv
Using target column: TARGET


[I 2024-07-08 15:30:27,144] Trial 0 finished with value: 0.909090909090909 and parameters: {'classifier': 'Random Forest', 'n_estimators': 167, 'max_depth': 25, 'min_samples_split': 4, 'min_samples_leaf': 3}. Best is trial 0 with value: 0.909090909090909.
[I 2024-07-08 15:30:27,170] Trial 1 finished with value: 0.9181818181818182 and parameters: {'classifier': 'Logistic Regression', 'C': 937.6027098298962, 'solver': 'lbfgs'}. Best is trial 1 with value: 0.9181818181818182.
[I 2024-07-08 15:30:27,237] Trial 2 finished with value: 0.9181818181818182 and parameters: {'classifier': 'Logistic Regression', 'C': 141.35471434589877, 'solver': 'newton-cg'}. Best is trial 1 with value: 0.9181818181818182.
[I 2024-07-08 15:30:27,436] Trial 3 finished with value: 0.9 and parameters: {'classifier': 'Gradient Boosting', 'n_estimators': 188, 'learning_rate': 0.01286048793154563, 'max_depth': 3, 'subsample': 0.9552643815886475}. Best is trial 1 with value: 0.9181818181818182.
[I 2024-07-08 15:30:27,70

...

[I 2024-07-08 15:48:19,890] A new study created in memory with name: no-name-cb7aca51-9bbc-4b0f-9d7d-92646e4161b0
[I 2024-07-08 15:48:19,918] Trial 0 finished with value: 0.9496753246753247 and parameters: {'classifier': 'Logistic Regression', 'C': 698.9728402667544, 'solver': 'lbfgs'}. Best is trial 0 with value: 0.9496753246753247.
[I 2024-07-08 15:48:19,967] Trial 1 finished with value: 0.9568831168831169 and parameters: {'classifier': 'XGBoost', 'n_estimators': 160, 'learning_rate': 0.013307282015798286, 'max_depth': 3, 'colsample_bytree': 0.6853845908833635}. Best is trial 1 with value: 0.9568831168831169.
[I 2024-07-08 15:48:19,993] Trial 2 finished with value: 0.9496753246753247 and parameters: {'classifier': 'Logistic Regression', 'C': 429.19173762386697, 'solver': 'newton-cg'}. Best is trial 1 with value: 0.9568831168831169.
[I 2024-07-08 15:48:20,009] Trial 3 finished with value: 0.9496753246753247 and parameters: {'classifier': 'Logistic Regression', 'C': 684.4407556786003, 

Number of finished trials:  100
Best trial:
  Value:  0.9568831168831169
  Params: 
    classifier: XGBoost
    n_estimators: 160
    learning_rate: 0.013307282015798286
    max_depth: 3
    colsample_bytree: 0.6853845908833635


[15:48:34] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.


Processing files:  50%|█████     | 135/270 [18:20<18:20,  8.16s/it]

Iteration 1, Accuracy: 0.9568345323741008, Improvement: 0.9568345323741008
Model saved at /content/exports/modelization/testing_data/constant_0/Isolation Forest/onehot/TARGET/best_XGBoost_model.pkl



/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [15:46:39] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [15:46:43] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [15:46:49] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [15:46:58] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [15:47:09] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encod

In [17]:
test_1 = pd.read_csv("./exports/manual_check_patch/testing_data/bfill/DBSCAN/ordinal/application_train.csv")

In [18]:
test_1["TARGET"].head()

0    0
1    1
2    0
3    0
4    0
Name: TARGET, dtype: int64

# Évaluation des Modèles

After training the models, the evaluate_models function is used to evaluate the performance of each model. This function calculates several performance metrics and also computes the business score based on the given formula.

Business Score Calculation
The business score is calculated using the following formula:

Business Score
=
(
Benefit
×
PPV
)
−
(
Cost
×
False Positive Rate
)
Business Score=(Benefit×PPV)−(Cost×False Positive Rate)

Where:

Benefit: The benefit obtained from a correct prediction.
PPV (Positive Predictive Value): 
TP
TP
+
FP
TP+FP
TP
​
 , where TP is the number of true positives and FP is the number of false positives.
Cost: The cost associated with an incorrect prediction.
False Positive Rate: 
FP
Total Negatives
Total Negatives
FP
​


In [53]:
# Assurez-vous que les fonctions plot_roc_curve et plot_confusion_matrix existent
def plot_roc_curve(y_test, y_pred_proba, model_name, output_dir):
    from sklearn.metrics import RocCurveDisplay
    RocCurveDisplay.from_predictions(y_test, y_pred_proba)
    plt.title(f'ROC Curve - {model_name}')
    plt.savefig(os.path.join(output_dir, f'roc_curve_{model_name}.png'))
    plt.close()

def plot_confusion_matrix(y_test, y_pred, model_name, output_dir):
    cm = confusion_matrix(y_test, y_pred)
    sns.heatmap(cm, annot=True, fmt='d', cmap='Blues')
    plt.title(f'Confusion Matrix - {model_name}')
    plt.ylabel('Actual')
    plt.xlabel('Predicted')
    plt.savefig(os.path.join(output_dir, f'confusion_matrix_{model_name}.png'))
    plt.close()

def evaluate_models(base_path, output_folder, target_columns, chunk_size=1000, benefit=1.0, cost=1.0):
    # Créer le dossier output_folder s'il n'existe pas
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    
    print(f"Output folder: {output_folder}")
    performance_metrics = []

    # Traverse base_path and find .pkl files
    for root, dirs, files in os.walk(base_path):
        for file in files:
            if file.endswith('.pkl'):
                model_path = os.path.join(root, file)
                model_name = file.split('_')[1] if len(file.split('_')) > 1 else "unknown_model"
                target_column = next((col for col in target_columns if col in root), None)

                if target_column:
                    print(f"Analyzing model: {model_name} for target: {target_column}")
                    try:
                        # Charger le modèle et les données de test
                        best_pipeline = joblib.load(model_path)
                        test_file_path = os.path.join(os.path.dirname(model_path), 'application_test.csv')
                        
                        if not os.path.exists(test_file_path):
                            print(f"Test file not found: {test_file_path}")
                            continue
                        
                        test_data = pd.read_csv(test_file_path, chunksize=chunk_size)
                        for chunk in test_data:
                            if target_column not in chunk.columns:
                                print(f"Target column {target_column} not in chunk columns")
                                continue

                            X_test = chunk.drop(target_column, axis=1)
                            y_test = chunk[target_column]

                            # Prédictions
                            y_pred = best_pipeline.predict(X_test)
                            y_pred_proba = best_pipeline.predict_proba(X_test)[:, 1]

                            # Calcul des métriques de performance
                            accuracy = accuracy_score(y_test, y_pred)
                            precision = precision_score(y_test, y_pred)
                            recall = recall_score(y_test, y_pred)
                            f1 = f1_score(y_test, y_pred)
                            roc_auc = roc_auc_score(y_test, y_pred_proba)

                            # Matrice de confusion
                            cm = confusion_matrix(y_test, y_pred)
                            TP = cm[1, 1]
                            FP = cm[0, 1]
                            TN = cm[0, 0]
                            FN = cm[1, 0]

                            # Calcul du VPP et Taux de faux positifs
                            VPP = TP / (TP + FP) if (TP + FP) > 0 else 0
                            taux_fp = FP / (FP + TN) if (FP + TN) > 0 else 0

                            # Calcul du Score Métier
                            score_metier = (benefit * VPP) - (cost * taux_fp)

                            performance_metrics.append({
                                'model': model_name,
                                'target': target_column,
                                'accuracy': accuracy,
                                'precision': precision,
                                'recall': recall,
                                'f1_score': f1,
                                'roc_auc': roc_auc,
                                'score_metier': score_metier
                            })

                            print(f"Accuracy: {accuracy}")
                            print(f"Precision: {precision}")
                            print(f"Recall: {recall}")
                            print(f"F1 Score: {f1}")
                            print(f"ROC AUC: {roc_auc}")
                            print(f"Score Métier: {score_metier}")

                            # Visualisation des résultats
                            plot_roc_curve(y_test, y_pred_proba, model_name, root)
                            plot_confusion_matrix(y_test, y_pred, model_name, root)
                    except Exception as e:
                        print(f"Error processing model {model_path}: {e}")

    if performance_metrics:
        # Convertir les métriques de performance en DataFrame
        performance_df = pd.DataFrame(performance_metrics)
        performance_df.to_csv(os.path.join(output_folder, 'model_performance_metrics.csv'), index=False)
        print("Performance metrics exported.")
        return performance_df
    else:
        print("No performance metrics to export.")
        return pd.DataFrame()

In [54]:
evaluate_models(
    base_path=LOCAL_EXPORT_MODELIZATION_FOLDER_PATH, 
    output_folder=LOCAL_EXPORT_MODELIZATION_EVALUATION_RESULT_FOLDER_PATH, 
    target_columns=["TARGET"], 
    chunk_size=GENERAL_CHUNK_SIZE, 
    benefit=1.0, 
    cost=1.0)

Output folder: /content/exports/modelization_evaluation
Analyzing model: Logistic Regression for target: TARGET
Test file not found: /content/exports/modelization/testing_data/mean/LOF/ordinal/TARGET/application_test.csv
Analyzing model: Logistic Regression for target: TARGET
Test file not found: /content/exports/modelization/testing_data/mean/LOF/label/TARGET/application_test.csv
Analyzing model: Logistic Regression for target: TARGET
Test file not found: /content/exports/modelization/testing_data/mean/LOF/onehot/TARGET/application_test.csv
Analyzing model: Random Forest for target: TARGET
Test file not found: /content/exports/modelization/testing_data/mean/DBSCAN/ordinal/TARGET/application_test.csv
Analyzing model: Random Forest for target: TARGET
Test file not found: /content/exports/modelization/testing_data/mean/DBSCAN/label/TARGET/application_test.csv
Analyzing model: Gradient Boosting for target: TARGET
Test file not found: /content/exports/modelization/testing_data/mean/DBSCAN/

Empty DataFrame
Columns: []
Index: []

/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [14:50:26] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [14:50:26] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [14:50:27] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [14:50:28] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.8/dist-packages/xgboost/core.py:158: UserWarning: [14:50:28] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encode

# Sélection du Modèle Final et Hyperparameter Tuning

After evaluating the models, the best performing model can be selected and further tuned using hyperparameter optimization.

def select_and_tune_best_model(performance_df, base_path, output_folder, target_column):
    best_model_row = performance_df.loc[performance_df['roc_auc'].idxmax()]
    best_model_name = best_model_row['model']
    print(f"Best model: {best_model_name} with ROC AUC: {best_model_row['roc_auc']}")

    model_path = os.path.join(output_folder, best_model_name, target_column, f'best_{best_model_name}_model.pkl')
    best_pipeline = joblib.load(model_path)

    # Tuning des hyperparamètres du meilleur modèle avec Optuna
    X_train = pd.read_csv(os.path.join(base_path, 'application_train.csv')).drop(target_column, axis=1)
    y_train = pd.read_csv(os.path.join(base_path, 'application_train.csv'))[target_column]

    study = optuna.create_study(direction='maximize')
    study.optimize(lambda trial: objective(trial, X_train, y_train), n_trials=100)

    print('Number of finished trials: ', len(study.trials))
    print('Best trial:')
    trial = study.best_trial

    print('  Value: ', trial.value)
    print('  Params: ')
    for key, value in trial.params.items():
        print('    {}: {}'.format(key, value))

    best_classifier = models[best_model_name]['model']
    best_params = {k: v for k, v in trial.params.items() if k != 'classifier'}
    best_classifier.set_params(**best_params)

    best_pipeline = Pipeline(steps=[
        ('classifier', best_classifier)
    ])

    best_pipeline.fit(X_train, y_train)
    joblib.dump(best_pipeline, model_path)
    print(f"Model saved at {model_path}")

    return best_pipeline

# Interprétabilité et Explicabilité
Using SHAP to explain the predictions of the model.

In [ ]:
def explain_model(best_pipeline, X_train, output_folder):
    explainer = shap.TreeExplainer(best_pipeline.named_steps['classifier'])
    shap_values = explainer.shap_values(X_train)

    shap.summary_plot(shap_values, X_train)
    plt.savefig(os.path.join(output_folder, 'shap_summary_plot.png'))
    plt.close()

    shap.initjs()
    shap.force_plot(explainer.expected_value, shap_values[0,:], X_train.iloc[0,:])
    plt.savefig(os.path.join(output_folder, 'shap_force_plot.png'))
    plt.close()

In [ ]:
# Summary

In [ ]:
def summarize_results(performance_df):
    best_model_row = performance_df.loc[performance_df['roc_auc'].idxmax()]
    best_model_name = best_model_row['model']
    summary = f"Best model: {best_model_name}\n"
    summary += f"Accuracy: {best_model_row['accuracy']}\n"
    summary += f"Precision: {best_model_row['precision']}\n"
    summary += f"Recall: {best_model_row['recall']}\n"
    summary += f"F1 Score: {best_model_row['f1_score']}\n"
    summary += f"ROC AUC: {best_model_row['roc_auc']}\n"
    summary += f"Business Score: {best_model_row['business_score']}\n"
    
    print(summary)

    with open(os.path.join(output_folder, 'model_summary.txt'), 'w') as f:
        f.write(summary)

    print("Summary saved.")